### Datasets merger script for RL_VPP_Thesis project

In [ ]:
%%capture
!pip install plotly==5.9.0

In [ ]:
import pandas as pd
import numpy as np
import plotly.express as px

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/data/
%ls

In [ ]:
#Moving to the current directory
current_folder = ''

input_folder = current_folder + 'data_validating/scenario_datasets/'
output_folder = current_folder + 'data_validating/environment_table/'

market_prices = pd.read_csv(input_folder + 'market_prices_2018_profile.csv')
PV_load = pd.read_csv(input_folder + 'PV_load_2018_profile.csv')
WT_load = pd.read_csv(input_folder + 'WT_load_2018_profile.csv')
household_load = pd.read_csv(input_folder + 'households_load_profile.csv')

In [ ]:
#Time indexes check
time_serie = market_prices["time"].values

assert(all(time_serie == PV_load["time"].values))
assert(all(time_serie == WT_load["time"].values))

#initialization of VPP table
VPP_table = pd.DataFrame({"time": time_serie})
VPP_table["time"] = pd.to_datetime(VPP_table["time"])

print(f"Total timesteps: {len(time_serie)}")

Total timesteps: 35041


In [ ]:
#Data preparation
household_load.rename(columns = {'power':'household_power'}, inplace = True) #kW
household_load.tail()

time  household_power
35036  2017-12-31 23:00:00         3.179217
35037  2017-12-31 23:15:00         3.072108
35038  2017-12-31 23:30:00         3.153099
35039  2017-12-31 23:45:00         3.239513
35040  2018-01-01 00:00:00         2.292833

In [ ]:
household_load["time"] = market_prices["time"]
assert(all(time_serie == household_load["time"].values))
household_load.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 35041 entries, 0 to 35040
Data columns (total 2 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   time             35041 non-null  object 
 1   household_power  35041 non-null  float64
dtypes: float64(1), object(1)
memory usage: 547.6+ KB


In [ ]:
#Merging of tables
VPP_table = pd.concat((VPP_table, household_load["household_power"], PV_load["solar_power"], WT_load["wind_power"], market_prices["EUR/kWh"] ), axis = 1)
VPP_table["renewable_power"] = VPP_table["solar_power"] + VPP_table["wind_power"]
VPP_table["House&RW_load"] = VPP_table["household_power"] - VPP_table["renewable_power"] #kW
VPP_table["total_cost"] = VPP_table["House&RW_load"] * VPP_table["EUR/kWh"] / 4

VPP_table = VPP_table.set_index("time")
VPP_table.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 35041 entries, 2018-01-01 00:00:00 to 2019-01-01 00:00:00
Data columns (total 7 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   household_power  35041 non-null  float64
 1   solar_power      35041 non-null  float64
 2   wind_power       35041 non-null  float64
 3   EUR/kWh          35041 non-null  float64
 4   renewable_power  35041 non-null  float64
 5   House&RW_load    35041 non-null  float64
 6   total_cost       35041 non-null  float64
dtypes: float64(7)
memory usage: 2.1 MB


In [ ]:
print("Energy consumed: kW", VPP_table["household_power"].sum()/4)
#VPP_table["household_power"].iplot(title='Households power', yTitle='kW', color='red')
px.line(VPP_table["household_power"], title=('Households power'), color_discrete_sequence=["red"]).update_layout(yaxis_title="kW", xaxis_rangeslider_visible=True, xaxis_range=["2018-06-01 00:00:00", "2018-07-01 00:00:00"])

Energy consumed: kW 20547.888190650003


In [ ]:
#VPP_table["solar_power"].iplot(title='Solar power', yTitle='kW')
px.line(VPP_table["solar_power"], title=('Solar power'), color_discrete_sequence=["orange"]).update_layout(yaxis_title="kW", xaxis_rangeslider_visible=True, xaxis_range=["2018-06-01 00:00:00", "2018-07-01 00:00:00"])

In [ ]:
#VPP_table["wind_power"].iplot(title='Wind power', yTitle='kW', color='cyan')
px.line(VPP_table["wind_power"], title=('Wind power'), color_discrete_sequence=["cyan"]).update_layout(yaxis_title="kW", xaxis_rangeslider_visible=True, xaxis_range=["2018-06-01 00:00:00", "2018-07-01 00:00:00"])

In [ ]:
print("Energy produced: kW", VPP_table["renewable_power"].sum()/4)
#VPP_table["renewable_power"].iplot(title='Renewable power', yTitle='kW', color='green')
px.line(VPP_table["renewable_power"], title=('Renewable power'), color_discrete_sequence=["green"]).update_layout(yaxis_title="kW", xaxis_rangeslider_visible=True, xaxis_range=["2018-06-01 00:00:00", "2018-07-01 00:00:00"])

Energy produced: kW 50633.276000000005


In [ ]:
HRW_array = np.array(VPP_table["House&RW_load"].values)
sum_HRW_power = np.sum((HRW_array)/4) #kWh
HRW_overenergy = HRW_array[HRW_array>0].sum()/4 #kWh
HRW_underenergy= HRW_array[HRW_array<0].sum()/4 #kWh

mean_HRW_power = np.mean(HRW_array)
std_HRW_power = np.std(HRW_array)
max_HRW_power = HRW_array[np.argmax(HRW_array)]
min_HRW_power = HRW_array[np.argmin(HRW_array)]
sum_HRW_power = np.sum(HRW_array/4)

print(f"Mean power rate: {round(mean_HRW_power,2)} kW, " +
        f"Std_power_rate: {round(std_HRW_power,2)} kW, " +
        f"Max_power_rate: {round(max_HRW_power,2)} kW, " +
        f"Min_power_rate: {round(min_HRW_power,2)} kW, " +
        f"Energy_summed: {round(sum_HRW_power,2)} kWh\n" +
        f"Energy_overconsumed: {round(HRW_overenergy,2)} kWh, " +
        f"Energy_underconsumed: {round(HRW_underenergy,2)} kWh")
#VPP_table["House&RW_load"].iplot(title='Households + Renewable power', yTitle='kW', color='blue')
#VPP_table["House&RW_load"].iplot(title='Households + Renewable power', yTitle='kW', color='blue')
px.line(VPP_table["House&RW_load"], title=('Households + Renewable power'), color_discrete_sequence=["blue"]).update_layout(yaxis_title="kW", xaxis_rangeslider_visible=True, xaxis_range=["2018-06-01 00:00:00", "2018-07-01 00:00:00"])

Mean power rate: -3.43 kW, Std_power_rate: 4.04 kW, Max_power_rate: 8.31 kW, Min_power_rate: -22.07 kW, Energy_summed: -30085.39 kWh
Energy_overconsumed: 2136.67 kWh, Energy_underconsumed: -32222.06 kWh


In [ ]:
cost_array = np.array(VPP_table["total_cost"].values)
print("Total cost = €", cost_array.sum(), ", Overcost = € ", cost_array[cost_array>0].sum())
#VPP_table["total_cost"].iplot(title='Cost', yTitle='€', color='violet')
px.line(VPP_table["total_cost"], title=('Cost'), color_discrete_sequence=["purple"]).update_layout(yaxis_title="€", xaxis_rangeslider_visible=True, xaxis_range=["2018-06-01 00:00:00", "2018-07-01 00:00:00"])

Total cost = € -1187.1491974157107 , Overcost = €  113.34279997735547


# Saving data in the repository

In [ ]:
VPP_table = VPP_table.drop(["renewable_power"], axis=1)
VPP_table_csv = VPP_table.to_csv(output_folder + 'Environment_data_2018.csv', index = True)